In [ ]:
# 安装 torch torchaudio torchvision
!pip install torch==2.0.0+cu118 torchaudio==2.0.1+cu118 torchvision==0.15.1+cu118 --index-url https://download.pytorch.org/whl/cu118

development

In [10]:
import torch
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:  
 print('Not connected to a GPU')
else:  
 print(gpu_info)
use_cuda = torch.cuda.is_available()

Sat Jan 31 12:40:00 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 576.40                 Driver Version: 576.40         CUDA Version: 12.9     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3090      WDDM  |   00000000:01:00.0  On |                  N/A |
|  0%   43C    P8             28W /  390W |    7970MiB /  24576MiB |     11%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [11]:
SEED = 42
WEIGHTED = True

In [12]:
from datasets import *
import pandas as pd
import numpy as np
train = pd.DataFrame(load_dataset("dev_phase2/subtask2/train/spa", split="train"))
val = pd.DataFrame(load_dataset("dev_phase2/subtask2/train/spa", split="train"))
test = pd.DataFrame(load_dataset("dev_phase2/subtask2/dev/spa", split="train"))
test_final = pd.DataFrame(load_dataset("test_phase/subtask2/test/spa", split="train"))
train.head()

id  \
0  spa_bc7bf0a1b710cd724cf96b5eeb020bff   
1  spa_688aec0f6abf4e0be44ecbfa886251cc   
2  spa_47019efabe7295c630bcc04bd0429230   
3  spa_8b4b244dbb90e0a813661ed12a1af5af   
4  spa_e2f37881da08b8d7b6eb07bc37356746   

                                                text  political  \
0  "bueno, tirando"\ny si hay repregunta, entonce...          0   
1                "caimos en su retorica de indigena"          0   
2   "cara de indigena sudaca", porque pio asi luego?          0   
3  "violar a una nina es menos grave que un abort...          0   
4              "yo decido quien es judio y quien no"          0   

   racial/ethnic  religious  gender/sexual  other  
0              0          0              0      0  
1              0          0              0      0  
2              0          0              0      0  
3              0          0              0      1  
4              1          0              0      0

In [13]:
labels = ["political", "racial/ethnic", "religious", "gender/sexual", "other"]
def get_text_and_label(df):  
  return df.rename(columns={"text": "text"})[["text"] + labels]
train = get_text_and_label(train)
print(f"Dataset size: <{len(train.index)}:{len(val.index)}:{len(test.index)}:{len(test_final.index)}>")
train.head(10)

Dataset size: <3305:3305:165:1488>


text  political  \
0  "bueno, tirando"\ny si hay repregunta, entonce...          0   
1                "caimos en su retorica de indigena"          0   
2   "cara de indigena sudaca", porque pio asi luego?          0   
3  "violar a una nina es menos grave que un abort...          0   
4              "yo decido quien es judio y quien no"          0   
5  #8m e cada dia en defensa dun xornalismo femin...          0   
6  #chvnoticias la muerte de ninos no se transa p...          0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...          1   
8  #ecuador | la cancilleria implementa plan de a...          0   
9  #importante | te decimos la ubicacion de los 1...          0   

   racial/ethnic  religious  gender/sexual  other  
0              0          0              0      0  
1              0          0              0      0  
2              0          0              0      0  
3              0          0              0      1  
4              1          0              0      0  
5              0          0              0      0  
6              1          1              0      0  
7              0          0              0      1  
8              0          0              0      0  
9              0          0              0      0

In [14]:
val = get_text_and_label(val)
val.head(10)

text  political  \
0  "bueno, tirando"\ny si hay repregunta, entonce...          0   
1                "caimos en su retorica de indigena"          0   
2   "cara de indigena sudaca", porque pio asi luego?          0   
3  "violar a una nina es menos grave que un abort...          0   
4              "yo decido quien es judio y quien no"          0   
5  #8m e cada dia en defensa dun xornalismo femin...          0   
6  #chvnoticias la muerte de ninos no se transa p...          0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...          1   
8  #ecuador | la cancilleria implementa plan de a...          0   
9  #importante | te decimos la ubicacion de los 1...          0   

   racial/ethnic  religious  gender/sexual  other  
0              0          0              0      0  
1              0          0              0      0  
2              0          0              0      0  
3              0          0              0      1  
4              1          0              0      0  
5              0          0              0      0  
6              1          1              0      0  
7              0          0              0      1  
8              0          0              0      0  
9              0          0              0      0

In [15]:
test = get_text_and_label(test)
test.head(10)

text political racial/ethnic  \
0  "puta weon, los progres arruinaron el indio pi...      None          None   
1  #mexico | el gobierno informo que esta dialoga...      None          None   
2               a abortar el mojon que traen atorado      None          None   
3             a comerrrrr\n(la salsa es curry indio)      None          None   
4                         aborto libre y retroactivo      None          None   
5  ah, veo que te has saltado las secuelas y el r...      None          None   
6            ase sina y corrupta , ella y su sequito      None          None   
7                           chak de india\n#indvseng      None          None   
8          coincred, a digital india.\n#coincredweb3      None          None   
9  corrupcion, corrupcion corrutos corrutos corru...      None          None   

  religious gender/sexual other  
0      None          None  None  
1      None          None  None  
2      None          None  None  
3      None          None  None  
4      None          None  None  
5      None          None  None  
6      None          None  None  
7      None          None  None  
8      None          None  None  
9      None          None  None

In [16]:
test_final = get_text_and_label(test_final)
test_final.head(10)

text political racial/ethnic  \
0  "penas severas para el aborto porque yo estuve...      None          None   
1              "si eres pobre debes abortar" eso lei      None          None   
2  #brasil exige a #eeuu "respeto" para repatriad...      None          None   
3  #honduras | el canciller anuncio la llegada de...      None          None   
4  #internacionales | el presidente de colombia, ...      None          None   
5            #karolsevilla #laliarg #kcamexico indio      None          None   
6  #mafiachotana #organizacioncriminal #corrupcio...      None          None   
7        , si tu no quieres, no tiene porque abortar      None          None   
8  -queee? pero si elon musk es judio.\n_y que ac...      None          None   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...      None          None   

  religious gender/sexual other  
0      None          None  None  
1      None          None  None  
2      None          None  None  
3      None          None  None  
4      None          None  None  
5      None          None  None  
6      None          None  None  
7      None          None  None  
8      None          None  None  
9      None          None  None

In [17]:
def generate_multilabel_df(df):
  df["labels"] = np.empty((len(df), len(labels))).tolist()
  for index, row in df.iterrows():
    row_labels = [row[label] for label in labels]
    for i in range(len(labels)):
      df.loc[index, "labels"][i] = row_labels[i]
  return df[["text", "labels"]]
train = generate_multilabel_df(train)
val = generate_multilabel_df(val)
test = generate_multilabel_df(test)
test_final = generate_multilabel_df(test_final)
train.head(10)

text           labels
0  "bueno, tirando"\ny si hay repregunta, entonce...  [0, 0, 0, 0, 0]
1                "caimos en su retorica de indigena"  [0, 0, 0, 0, 0]
2   "cara de indigena sudaca", porque pio asi luego?  [0, 0, 0, 0, 0]
3  "violar a una nina es menos grave que un abort...  [0, 0, 0, 0, 1]
4              "yo decido quien es judio y quien no"  [0, 1, 0, 0, 0]
5  #8m e cada dia en defensa dun xornalismo femin...  [0, 0, 0, 0, 0]
6  #chvnoticias la muerte de ninos no se transa p...  [0, 1, 1, 0, 0]
7  #corrupcion#prensa#desestabilizadora#nido#rata...  [1, 0, 0, 0, 1]
8  #ecuador | la cancilleria implementa plan de a...  [0, 0, 0, 0, 0]
9  #importante | te decimos la ubicacion de los 1...  [0, 0, 0, 0, 0]

In [18]:
test.head(10)

text  \
0  "puta weon, los progres arruinaron el indio pi...   
1  #mexico | el gobierno informo que esta dialoga...   
2               a abortar el mojon que traen atorado   
3             a comerrrrr\n(la salsa es curry indio)   
4                         aborto libre y retroactivo   
5  ah, veo que te has saltado las secuelas y el r...   
6            ase sina y corrupta , ella y su sequito   
7                           chak de india\n#indvseng   
8          coincred, a digital india.\n#coincredweb3   
9  corrupcion, corrupcion corrutos corrutos corru...   

                           labels  
0  [None, None, None, None, None]  
1  [None, None, None, None, None]  
2  [None, None, None, None, None]  
3  [None, None, None, None, None]  
4  [None, None, None, None, None]  
5  [None, None, None, None, None]  
6  [None, None, None, None, None]  
7  [None, None, None, None, None]  
8  [None, None, None, None, None]  
9  [None, None, None, None, None]

In [19]:
test_final.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                           labels  
0  [None, None, None, None, None]  
1  [None, None, None, None, None]  
2  [None, None, None, None, None]  
3  [None, None, None, None, None]  
4  [None, None, None, None, None]  
5  [None, None, None, None, None]  
6  [None, None, None, None, None]  
7  [None, None, None, None, None]  
8  [None, None, None, None, None]  
9  [None, None, None, None, None]

In [20]:
from datetime import datetime, timedelta
import os
PATH = "./outputs/{}/".format((datetime.now() + timedelta(hours=2)).strftime("%d-%m-%Y-%H-%M"))
print("Current working dir:", PATH)
os.mkdir(PATH)

Current working dir: ./outputs/31-01-2026-14-43/


In [21]:
models = {
    "mbert-cased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-cased"
    },
    "mbert-uncased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-uncased"
    },
    "roberta": {
        "model_type": "roberta",
        "model_name": "models--FacebookAI--roberta-base"
    },
    "beto-cased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-cased"
    },
    "beto-uncased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-uncased"
    },
    "distilbert-multi": {
        "model_type": "distilbert",
        "model_name": "models--distilbert--distilbert-base-multilingual-cased"
    }
}

In [22]:
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
for model, fields in models.items():
  model_args = MultiLabelClassificationArgs(
      overwrite_output_dir= True,
      eval_batch_size=8,
      num_train_epochs=5,
      learning_rate = 4e-05,
      optimizer="AdamW",
      manual_seed=SEED,
      use_early_stopping=True,
      save_model_every_epoch=False
  )
  model_args.output_dir = os.path.join(PATH, model)
  models[model] = MultiLabelClassificationModel(fields["model_type"], fields["model_name"],
                                      args=model_args, num_labels=len(labels), use_cuda=use_cuda)

Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--FacebookAI--roberta-base and are newly initialized: ['roberta.pooler.dense.weight', 'classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.weight', 'roberta.pooler.dense.bias', 'classifier.d

In [23]:
from sklearn.metrics import mean_squared_error
from math import sqrt
def root_mean_squared_error(y_true, y_pred):    
  return sqrt(mean_squared_error(y_true, y_pred))

In [ ]:
for model_name, model in models.items():
  model.train_model(train, loss_fct=root_mean_squared_error)

7it [00:04,  1.54it/s]                                                                                                                                                                                                                  
Epochs 5/5. Running Loss:    0.3504:  13%|████████████████████▊                                                                                                                                        | 55/414 [00:04<00:28, 12.57it/s]

Epochs 1/5. Running Loss:    0.3902:  84%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊                         | 347/414 [00:15<00:02, 26.34it/s]

In [35]:
import collections
from itertools import combinations
models_names = list(models.keys())
ensembles_list = list()
for i in range(1, len(models_names) + 1):
    ensembles_list += list(combinations(models_names, i))
ensembles_list = [list(ensemble) for ensemble in ensembles_list]
ensembles = {}
for i in range(len(ensembles_list)):
  ensembles["ensemble{:02d}".format(i)] = {}
  ensembles["ensemble{:02d}".format(i)]["models"] = ensembles_list[i]
  ensembles["ensemble{:02d}".format(i)]["metrics"] = {}
ensembles

{'ensemble00': {'models': ['mbert-cased'], 'metrics': {}},
 'ensemble01': {'models': ['mbert-uncased'], 'metrics': {}},
 'ensemble02': {'models': ['roberta'], 'metrics': {}},
 'ensemble03': {'models': ['beto-cased'], 'metrics': {}},
 'ensemble04': {'models': ['beto-uncased'], 'metrics': {}},
 'ensemble05': {'models': ['distilbert-multi'], 'metrics': {}},
 'ensemble06': {'models': ['mbert-cased', 'mbert-uncased'], 'metrics': {}},
 'ensemble07': {'models': ['mbert-cased', 'roberta'], 'metrics': {}},
 'ensemble08': {'models': ['mbert-cased', 'beto-cased'], 'metrics': {}},
 'ensemble09': {'models': ['mbert-cased', 'beto-uncased'], 'metrics': {}},
 'ensemble10': {'models': ['mbert-cased', 'distilbert-multi'], 'metrics': {}},
 'ensemble11': {'models': ['mbert-uncased', 'roberta'], 'metrics': {}},
 'ensemble12': {'models': ['mbert-uncased', 'beto-cased'], 'metrics': {}},
 'ensemble13': {'models': ['mbert-uncased', 'beto-uncased'], 'metrics': {}},
 'ensemble14': {'models': ['mbert-uncased', 'd

In [36]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, f1_score
def compute_metrics(y_true, y_pred):
  macro_precision, macro_recall, macro_f1, _ = precision_recall_fscore_support(y_true, y_pred, average='macro')
  acc = accuracy_score(y_true, y_pred)
  weighted_f1 = f1_score(y_true, y_pred, average='weighted')
  return {
      'accuracy': round(acc, 5),
      'macro_f1': round(macro_f1, 5),
      'macro_precision': round(macro_precision, 5),
      'macro_recall': round(macro_recall, 5),
      'weighted_f1': round(weighted_f1, 5)
  }
model_evaluation = {}
for model_name in models:
  model_evaluation[model_name] = {}
  result, model_outputs, wrong_predictions = models[model_name].eval_model(val, metric=root_mean_squared_error)
  model_evaluation[model_name]["result"] = result                                                                   
  model_evaluation[model_name]["val_model_outputs"] = model_outputs                                                 
  model_evaluation[model_name]["val_predictions"] = list ()
  for output in model_outputs:
    model_evaluation[model_name]["val_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output]) 
  model_evaluation[model_name]["val_wrong_predictions"] = wrong_predictions                                         
  model_evaluation[model_name]["metrics"] = compute_metrics(val.get("labels").tolist(), model_evaluation[model_name].get("val_predictions"))
  print(f"{model_name}\t", model_evaluation[model_name].get("metrics"))

7it [00:04,  1.51it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 78.57it/s]


mbert-cased	 {'accuracy': 0.85809, 'macro_f1': 0.89211, 'macro_precision': 0.93471, 'macro_recall': 0.85738, 'weighted_f1': 0.89993}


7it [00:04,  1.59it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 82.65it/s]


mbert-uncased	 {'accuracy': 0.89864, 'macro_f1': 0.92486, 'macro_precision': 0.95456, 'macro_recall': 0.89841, 'weighted_f1': 0.92861}


7it [00:04,  1.59it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 78.17it/s]


...

beto-cased	 {'accuracy': 0.95613, 'macro_f1': 0.97132, 'macro_precision': 0.98452, 'macro_recall': 0.95872, 'weighted_f1': 0.97262}


7it [00:04,  1.63it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:04<00:00, 84.62it/s]


beto-uncased	 {'accuracy': 0.96702, 'macro_f1': 0.97754, 'macro_precision': 0.9932, 'macro_recall': 0.96255, 'weighted_f1': 0.97933}


7it [00:04,  1.56it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:02<00:00, 138.92it/s]


distilbert-multi	 {'accuracy': 0.87352, 'macro_f1': 0.90232, 'macro_precision': 0.94202, 'macro_recall': 0.86808, 'weighted_f1': 0.90798}


In [37]:
from sklearn.preprocessing import normalize
def vote(predictions, weighted=False, weights=None):
  votes = list()  
  for i in range(len(labels)):    
    curr_label_preds = [preds[i] for preds in predictions]    
    voting = sum(curr_label_preds * weights) if weighted else sum(curr_label_preds)/len(curr_label_preds)
    votes.append(0 if voting < 0.5 else 1)  
  return votes
ensemble_evaluation = {}
def predict_ensemble(ensemble_name, dataset_name, dataset, weighted=False):
  ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"] = list()  
  for i in range(len(dataset.index)):
    predictions = list()
    ensemble_models = ensembles[ensemble_name].get("models")      
    for model_name in ensemble_models:
      curr_model_outputs = model_evaluation[model_name].get(f"{dataset_name}_model_outputs")
      predictions.append(curr_model_outputs[i])
    weights = list()    
    if weighted:      
      f1_scores_list = [model_evaluation[model_name]["metrics"].get("weighted_f1")                        
                        for model_name in ensembles[ensemble_name].get("models")]
      weights = normalize([f1_scores_list], norm="l1")[0]
    ensemble_pred = vote(predictions, weighted, weights)
    ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"].append(ensemble_pred)
for ensemble_name in ensembles:
  ensemble_evaluation[ensemble_name] = {}
  ensemble_evaluation[ensemble_name]["val_predictions"] = list()
  predict_ensemble(ensemble_name, "val", val, weighted=WEIGHTED)
  ensembles[ensemble_name]["metrics"] = compute_metrics(val.get("labels").tolist(), ensemble_evaluation[ensemble_name].get("val_predictions"))  
  print(f"{ensemble_name}\t", ensembles[ensemble_name].get("metrics"))

ensemble00	 {'accuracy': 0.85809, 'macro_f1': 0.89211, 'macro_precision': 0.93471, 'macro_recall': 0.85738, 'weighted_f1': 0.89993}
ensemble01	 {'accuracy': 0.89864, 'macro_f1': 0.92486, 'macro_precision': 0.95456, 'macro_recall': 0.89841, 'weighted_f1': 0.92861}
ensemble02	 {'accuracy': 0.68351, 'macro_f1': 0.73996, 'macro_precision': 0.77952, 'macro_recall': 0.70811, 'weighted_f1': 0.7513}
ensemble03	 {'accuracy': 0.95613, 'macro_f1': 0.97132, 'macro_precision': 0.98452, 'macro_recall': 0.95872, 'weighted_f1': 0.97262}
ensemble04	 {'accuracy': 0.96702, 'macro_f1': 0.97754, 'macro_precision': 0.9932, 'macro_recall': 0.96255, 'weighted_f1': 0.97933}
ensemble05	 {'accuracy': 0.87352, 'macro_f1': 0.90232, 'macro_precision': 0.94202, 'macro_recall': 0.86808, 'weighted_f1': 0.90798}
ensemble06	 {'accuracy': 0.89924, 'macro_f1': 0.92439, 'macro_precision': 0.95952, 'macro_recall': 0.89369, 'weighted_f1': 0.9291}
ensemble07	 {'accuracy': 0.84024, 'macro_f1': 0.87703, 'macro_precision': 0.928

In [38]:
import json
with open(os.path.join(PATH, 'ensembles.json'), 'w', encoding='utf-8') as f:
    json.dump(ensembles, f, ensure_ascii=False, indent=4)

In [39]:
f1_scores = {ensemble_name: ensembles[ensemble_name]["metrics"].get("weighted_f1") for ensemble_name in ensemble_evaluation}
best_ensemble_name = max(f1_scores, key=f1_scores.get)
best_ensemble = {"name": best_ensemble_name,                 
                "models": ensembles[best_ensemble_name].get("models"),                 
                "metrics": ensembles[best_ensemble_name].get("metrics")                 
                }
best_ensemble

{'name': 'ensemble18',
 'models': ['beto-cased', 'beto-uncased'],
 'metrics': {'accuracy': 0.97035,
  'macro_f1': 0.98024,
  'macro_precision': 0.99442,
  'macro_recall': 0.96671,
  'weighted_f1': 0.98177}}

In [30]:
for model_name in models:
  model_predictions, model_raw_outputs = models.get(model_name).predict(test["text"].tolist())
  model_evaluation[model_name]["test_model_outputs"] = model_raw_outputs
  model_evaluation[model_name]["test_predictions"] = list ()  
  for output in model_raw_outputs:
    model_evaluation[model_name]["test_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output])
predict_ensemble(best_ensemble.get("name"), "test", test, weighted=WEIGHTED)

1it [00:03,  3.38s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 40.19it/s]
1it [00:03,  3.15s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 45.56it/s]
1it [00:03,  3.08s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 41.19it/s]
1it [00:03,  3.24s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [

In [31]:
for model_name, evaluation in model_evaluation.items():
  curr_model = model_evaluation.get(model_name)
  curr_model["val_model_outputs"] = [list(output) for output in curr_model.get("val_model_outputs")]
  curr_model["test_model_outputs"] = [list(output) for output in curr_model.get("test_model_outputs")]
  curr_model["val_predictions"] = list(curr_model.get("val_predictions"))
  curr_model["test_predictions"] = list(curr_model.get("test_predictions"))
  if curr_model.get("val_wrong_predictions"):
    curr_model["val_wrong_predictions_list"] = curr_model.get("val_wrong_predictions")
    curr_model["val_wrong_predictions"] = {}
    for pred in curr_model.get("val_wrong_predictions_list"):
      curr_model["val_wrong_predictions"][pred.guid] = {
          "text_a": pred.text_a,
          "text_b": pred.text_b,
          "label": pred.label
      }
    del curr_model["val_wrong_predictions_list"]

  with open(os.path.join(PATH, f'{model_name}/model-evaluation.json'), 'w', encoding='utf-8') as f:
    json.dump(curr_model, f, ensure_ascii=False, indent=4)

In [32]:
best_ensemble["val_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("val_predictions")
best_ensemble["test_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
with open(os.path.join(PATH, 'best-ensemble.json'), 'w', encoding='utf-8') as f:
    json.dump(best_ensemble, f, ensure_ascii=False, indent=4)

In [33]:
test["predicted_labels"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
test.head(10)

text  \
0  "puta weon, los progres arruinaron el indio pi...   
1  #mexico | el gobierno informo que esta dialoga...   
2               a abortar el mojon que traen atorado   
3             a comerrrrr\n(la salsa es curry indio)   
4                         aborto libre y retroactivo   
5  ah, veo que te has saltado las secuelas y el r...   
6            ase sina y corrupta , ella y su sequito   
7                           chak de india\n#indvseng   
8          coincred, a digital india.\n#coincredweb3   
9  corrupcion, corrupcion corrutos corrutos corru...   

                           labels predicted_labels  
0  [None, None, None, None, None]  [0, 1, 0, 0, 0]  
1  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
2  [None, None, None, None, None]  [0, 0, 0, 0, 1]  
3  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
4  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
5  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
6  [None, None, None, None, None]  [1, 0, 0, 0, 1]  
7  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
8  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
9  [None, None, None, None, None]  [1, 0, 0, 0, 0]

In [34]:
test.to_csv(os.path.join(PATH, "test-predictions.csv"), index=False)  

test

In [62]:
import torch
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:  
 print('Not connected to a GPU')
else:  
 print(gpu_info)
use_cuda = torch.cuda.is_available()

Sat Jan 31 13:57:49 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 576.40                 Driver Version: 576.40         CUDA Version: 12.9     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3090      WDDM  |   00000000:01:00.0  On |                  N/A |
|  0%   44C    P8             28W /  390W |   14522MiB /  24576MiB |     11%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [63]:
SEED = 42
WEIGHTED = True

In [64]:
from datasets import *
import pandas as pd
import numpy as np
train = pd.DataFrame(load_dataset("dev_phase2/subtask2/train/spa", split="train"))
val = pd.DataFrame(load_dataset("dev_phase2/subtask2/train/spa", split="train"))
test = pd.DataFrame(load_dataset("dev_phase2/subtask2/dev/spa", split="train"))
test_final = pd.DataFrame(load_dataset("test_phase/subtask2/test/spa", split="train"))
train.head()

id  \
0  spa_bc7bf0a1b710cd724cf96b5eeb020bff   
1  spa_688aec0f6abf4e0be44ecbfa886251cc   
2  spa_47019efabe7295c630bcc04bd0429230   
3  spa_8b4b244dbb90e0a813661ed12a1af5af   
4  spa_e2f37881da08b8d7b6eb07bc37356746   

                                                text  political  \
0  "bueno, tirando"\ny si hay repregunta, entonce...          0   
1                "caimos en su retorica de indigena"          0   
2   "cara de indigena sudaca", porque pio asi luego?          0   
3  "violar a una nina es menos grave que un abort...          0   
4              "yo decido quien es judio y quien no"          0   

   racial/ethnic  religious  gender/sexual  other  
0              0          0              0      0  
1              0          0              0      0  
2              0          0              0      0  
3              0          0              0      1  
4              1          0              0      0

In [65]:
labels = ["political", "racial/ethnic", "religious", "gender/sexual", "other"]
def get_text_and_label(df):  
  return df.rename(columns={"text": "text"})[["text"] + labels]
train = get_text_and_label(train)
print(f"Dataset size: <{len(train.index)}:{len(val.index)}:{len(test.index)}:{len(test_final.index)}>")
train.head(10)

Dataset size: <3305:3305:165:1488>


text  political  \
0  "bueno, tirando"\ny si hay repregunta, entonce...          0   
1                "caimos en su retorica de indigena"          0   
2   "cara de indigena sudaca", porque pio asi luego?          0   
3  "violar a una nina es menos grave que un abort...          0   
4              "yo decido quien es judio y quien no"          0   
5  #8m e cada dia en defensa dun xornalismo femin...          0   
6  #chvnoticias la muerte de ninos no se transa p...          0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...          1   
8  #ecuador | la cancilleria implementa plan de a...          0   
9  #importante | te decimos la ubicacion de los 1...          0   

   racial/ethnic  religious  gender/sexual  other  
0              0          0              0      0  
1              0          0              0      0  
2              0          0              0      0  
3              0          0              0      1  
4              1          0              0      0  
5              0          0              0      0  
6              1          1              0      0  
7              0          0              0      1  
8              0          0              0      0  
9              0          0              0      0

In [66]:
val = get_text_and_label(val)
val.head(10)

text  political  \
0  "bueno, tirando"\ny si hay repregunta, entonce...          0   
1                "caimos en su retorica de indigena"          0   
2   "cara de indigena sudaca", porque pio asi luego?          0   
3  "violar a una nina es menos grave que un abort...          0   
4              "yo decido quien es judio y quien no"          0   
5  #8m e cada dia en defensa dun xornalismo femin...          0   
6  #chvnoticias la muerte de ninos no se transa p...          0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...          1   
8  #ecuador | la cancilleria implementa plan de a...          0   
9  #importante | te decimos la ubicacion de los 1...          0   

   racial/ethnic  religious  gender/sexual  other  
0              0          0              0      0  
1              0          0              0      0  
2              0          0              0      0  
3              0          0              0      1  
4              1          0              0      0  
5              0          0              0      0  
6              1          1              0      0  
7              0          0              0      1  
8              0          0              0      0  
9              0          0              0      0

In [67]:
test = get_text_and_label(test)
test.head(10)

text political racial/ethnic  \
0  "puta weon, los progres arruinaron el indio pi...      None          None   
1  #mexico | el gobierno informo que esta dialoga...      None          None   
2               a abortar el mojon que traen atorado      None          None   
3             a comerrrrr\n(la salsa es curry indio)      None          None   
4                         aborto libre y retroactivo      None          None   
5  ah, veo que te has saltado las secuelas y el r...      None          None   
6            ase sina y corrupta , ella y su sequito      None          None   
7                           chak de india\n#indvseng      None          None   
8          coincred, a digital india.\n#coincredweb3      None          None   
9  corrupcion, corrupcion corrutos corrutos corru...      None          None   

  religious gender/sexual other  
0      None          None  None  
1      None          None  None  
2      None          None  None  
3      None          None  None  
4      None          None  None  
5      None          None  None  
6      None          None  None  
7      None          None  None  
8      None          None  None  
9      None          None  None

In [68]:
test_final = get_text_and_label(test_final)
test_final.head(10)

text political racial/ethnic  \
0  "penas severas para el aborto porque yo estuve...      None          None   
1              "si eres pobre debes abortar" eso lei      None          None   
2  #brasil exige a #eeuu "respeto" para repatriad...      None          None   
3  #honduras | el canciller anuncio la llegada de...      None          None   
4  #internacionales | el presidente de colombia, ...      None          None   
5            #karolsevilla #laliarg #kcamexico indio      None          None   
6  #mafiachotana #organizacioncriminal #corrupcio...      None          None   
7        , si tu no quieres, no tiene porque abortar      None          None   
8  -queee? pero si elon musk es judio.\n_y que ac...      None          None   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...      None          None   

  religious gender/sexual other  
0      None          None  None  
1      None          None  None  
2      None          None  None  
3      None          None  None  
4      None          None  None  
5      None          None  None  
6      None          None  None  
7      None          None  None  
8      None          None  None  
9      None          None  None

In [69]:
def generate_multilabel_df(df):
  df["labels"] = np.empty((len(df), len(labels))).tolist()
  for index, row in df.iterrows():
    row_labels = [row[label] for label in labels]
    for i in range(len(labels)):
      df.loc[index, "labels"][i] = row_labels[i]
  return df[["text", "labels"]]
train = generate_multilabel_df(train)
val = generate_multilabel_df(val)
test = generate_multilabel_df(test)
test_final = generate_multilabel_df(test_final)
train.head(10)

text           labels
0  "bueno, tirando"\ny si hay repregunta, entonce...  [0, 0, 0, 0, 0]
1                "caimos en su retorica de indigena"  [0, 0, 0, 0, 0]
2   "cara de indigena sudaca", porque pio asi luego?  [0, 0, 0, 0, 0]
3  "violar a una nina es menos grave que un abort...  [0, 0, 0, 0, 1]
4              "yo decido quien es judio y quien no"  [0, 1, 0, 0, 0]
5  #8m e cada dia en defensa dun xornalismo femin...  [0, 0, 0, 0, 0]
6  #chvnoticias la muerte de ninos no se transa p...  [0, 1, 1, 0, 0]
7  #corrupcion#prensa#desestabilizadora#nido#rata...  [1, 0, 0, 0, 1]
8  #ecuador | la cancilleria implementa plan de a...  [0, 0, 0, 0, 0]
9  #importante | te decimos la ubicacion de los 1...  [0, 0, 0, 0, 0]

In [70]:
test.head(10)

text  \
0  "puta weon, los progres arruinaron el indio pi...   
1  #mexico | el gobierno informo que esta dialoga...   
2               a abortar el mojon que traen atorado   
3             a comerrrrr\n(la salsa es curry indio)   
4                         aborto libre y retroactivo   
5  ah, veo que te has saltado las secuelas y el r...   
6            ase sina y corrupta , ella y su sequito   
7                           chak de india\n#indvseng   
8          coincred, a digital india.\n#coincredweb3   
9  corrupcion, corrupcion corrutos corrutos corru...   

                           labels  
0  [None, None, None, None, None]  
1  [None, None, None, None, None]  
2  [None, None, None, None, None]  
3  [None, None, None, None, None]  
4  [None, None, None, None, None]  
5  [None, None, None, None, None]  
6  [None, None, None, None, None]  
7  [None, None, None, None, None]  
8  [None, None, None, None, None]  
9  [None, None, None, None, None]

In [71]:
test_final.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                           labels  
0  [None, None, None, None, None]  
1  [None, None, None, None, None]  
2  [None, None, None, None, None]  
3  [None, None, None, None, None]  
4  [None, None, None, None, None]  
5  [None, None, None, None, None]  
6  [None, None, None, None, None]  
7  [None, None, None, None, None]  
8  [None, None, None, None, None]  
9  [None, None, None, None, None]

In [72]:
test = test_final
test.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                           labels  
0  [None, None, None, None, None]  
1  [None, None, None, None, None]  
2  [None, None, None, None, None]  
3  [None, None, None, None, None]  
4  [None, None, None, None, None]  
5  [None, None, None, None, None]  
6  [None, None, None, None, None]  
7  [None, None, None, None, None]  
8  [None, None, None, None, None]  
9  [None, None, None, None, None]

In [73]:
from datetime import datetime, timedelta
import os
PATH = "./outputs/{}/".format((datetime.now() + timedelta(hours=2)).strftime("%d-%m-%Y-%H-%M"))
print("Current working dir:", PATH)
os.mkdir(PATH)

Current working dir: ./outputs/31-01-2026-15-58/


In [74]:
models = {
    "mbert-cased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-cased"
    },
    "mbert-uncased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-uncased"
    },
    "roberta": {
        "model_type": "roberta",
        "model_name": "models--FacebookAI--roberta-base"
    },
    "beto-cased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-cased"
    },
    "beto-uncased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-uncased"
    },
    "distilbert-multi": {
        "model_type": "distilbert",
        "model_name": "models--distilbert--distilbert-base-multilingual-cased"
    }
}

In [75]:
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
for model, fields in models.items():
  model_args = MultiLabelClassificationArgs(
      overwrite_output_dir= True,
      eval_batch_size=8,
      num_train_epochs=5,
      learning_rate = 4e-05,
      optimizer="AdamW",
      manual_seed=SEED,
      use_early_stopping=True,
      save_model_every_epoch=False
  )
  model_args.output_dir = os.path.join(PATH, model)
  models[model] = MultiLabelClassificationModel(fields["model_type"], fields["model_name"],
                                      args=model_args, num_labels=len(labels), use_cuda=use_cuda)

Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--FacebookAI--roberta-base and are newly initialized: ['roberta.pooler.dense.weight', 'classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.weight', 'roberta.pooler.dense.bias', 'classifier.d

In [76]:
from sklearn.metrics import mean_squared_error
from math import sqrt
def root_mean_squared_error(y_true, y_pred):    
  return sqrt(mean_squared_error(y_true, y_pred))

In [ ]:
for model_name, model in models.items():
  model.train_model(train, loss_fct=root_mean_squared_error)

7it [00:04,  1.42it/s]                                                                                                                                                                                                                  
Epochs 2/5. Running Loss:    0.3503:  95%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍       | 394/414 [00:24<00:01, 17.83it/s]

Epochs 2/5. Running Loss:    0.3104:  33%|██████████████████████████████████████████████████▊                                                                                                         | 135/414 [00:07<00:14, 19.15it/s]

In [81]:
import collections
from itertools import combinations
models_names = list(models.keys())
ensembles_list = list()
for i in range(1, len(models_names) + 1):
    ensembles_list += list(combinations(models_names, i))
ensembles_list = [list(ensemble) for ensemble in ensembles_list]
ensembles = {}
for i in range(len(ensembles_list)):
  ensembles["ensemble{:02d}".format(i)] = {}
  ensembles["ensemble{:02d}".format(i)]["models"] = ensembles_list[i]
  ensembles["ensemble{:02d}".format(i)]["metrics"] = {}
ensembles

{'ensemble00': {'models': ['mbert-cased'], 'metrics': {}},
 'ensemble01': {'models': ['mbert-uncased'], 'metrics': {}},
 'ensemble02': {'models': ['roberta'], 'metrics': {}},
 'ensemble03': {'models': ['beto-cased'], 'metrics': {}},
 'ensemble04': {'models': ['beto-uncased'], 'metrics': {}},
 'ensemble05': {'models': ['distilbert-multi'], 'metrics': {}},
 'ensemble06': {'models': ['mbert-cased', 'mbert-uncased'], 'metrics': {}},
 'ensemble07': {'models': ['mbert-cased', 'roberta'], 'metrics': {}},
 'ensemble08': {'models': ['mbert-cased', 'beto-cased'], 'metrics': {}},
 'ensemble09': {'models': ['mbert-cased', 'beto-uncased'], 'metrics': {}},
 'ensemble10': {'models': ['mbert-cased', 'distilbert-multi'], 'metrics': {}},
 'ensemble11': {'models': ['mbert-uncased', 'roberta'], 'metrics': {}},
 'ensemble12': {'models': ['mbert-uncased', 'beto-cased'], 'metrics': {}},
 'ensemble13': {'models': ['mbert-uncased', 'beto-uncased'], 'metrics': {}},
 'ensemble14': {'models': ['mbert-uncased', 'd

In [82]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, f1_score
def compute_metrics(y_true, y_pred):
  macro_precision, macro_recall, macro_f1, _ = precision_recall_fscore_support(y_true, y_pred, average='macro')
  acc = accuracy_score(y_true, y_pred)
  weighted_f1 = f1_score(y_true, y_pred, average='weighted')
  return {
      'accuracy': round(acc, 5),
      'macro_f1': round(macro_f1, 5),
      'macro_precision': round(macro_precision, 5),
      'macro_recall': round(macro_recall, 5),
      'weighted_f1': round(weighted_f1, 5)
  }
model_evaluation = {}
for model_name in models:
  model_evaluation[model_name] = {}
  result, model_outputs, wrong_predictions = models[model_name].eval_model(val, metric=root_mean_squared_error)
  model_evaluation[model_name]["result"] = result                                                                   
  model_evaluation[model_name]["val_model_outputs"] = model_outputs                                                 
  model_evaluation[model_name]["val_predictions"] = list ()
  for output in model_outputs:
    model_evaluation[model_name]["val_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output]) 
  model_evaluation[model_name]["val_wrong_predictions"] = wrong_predictions                                         
  model_evaluation[model_name]["metrics"] = compute_metrics(val.get("labels").tolist(), model_evaluation[model_name].get("val_predictions"))
  print(f"{model_name}\t", model_evaluation[model_name].get("metrics"))

7it [00:04,  1.44it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 79.72it/s]


mbert-cased	 {'accuracy': 0.85809, 'macro_f1': 0.89211, 'macro_precision': 0.93471, 'macro_recall': 0.85738, 'weighted_f1': 0.89993}


7it [00:04,  1.51it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 81.07it/s]


mbert-uncased	 {'accuracy': 0.89864, 'macro_f1': 0.92486, 'macro_precision': 0.95456, 'macro_recall': 0.89841, 'weighted_f1': 0.92861}


7it [00:04,  1.63it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:04<00:00, 85.23it/s]


...

beto-cased	 {'accuracy': 0.95613, 'macro_f1': 0.97132, 'macro_precision': 0.98452, 'macro_recall': 0.95872, 'weighted_f1': 0.97262}


7it [00:04,  1.68it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:04<00:00, 87.74it/s]


beto-uncased	 {'accuracy': 0.96702, 'macro_f1': 0.97754, 'macro_precision': 0.9932, 'macro_recall': 0.96255, 'weighted_f1': 0.97933}


7it [00:04,  1.61it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:02<00:00, 143.31it/s]


distilbert-multi	 {'accuracy': 0.87352, 'macro_f1': 0.90232, 'macro_precision': 0.94202, 'macro_recall': 0.86808, 'weighted_f1': 0.90798}


In [83]:
from sklearn.preprocessing import normalize
def vote(predictions, weighted=False, weights=None):
  votes = list()  
  for i in range(len(labels)):    
    curr_label_preds = [preds[i] for preds in predictions]    
    voting = sum(curr_label_preds * weights) if weighted else sum(curr_label_preds)/len(curr_label_preds)
    votes.append(0 if voting < 0.5 else 1)  
  return votes
ensemble_evaluation = {}
def predict_ensemble(ensemble_name, dataset_name, dataset, weighted=False):
  ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"] = list()  
  for i in range(len(dataset.index)):
    predictions = list()
    ensemble_models = ensembles[ensemble_name].get("models")      
    for model_name in ensemble_models:
      curr_model_outputs = model_evaluation[model_name].get(f"{dataset_name}_model_outputs")
      predictions.append(curr_model_outputs[i])
    weights = list()    
    if weighted:      
      f1_scores_list = [model_evaluation[model_name]["metrics"].get("weighted_f1")                        
                        for model_name in ensembles[ensemble_name].get("models")]
      weights = normalize([f1_scores_list], norm="l1")[0]
    ensemble_pred = vote(predictions, weighted, weights)
    ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"].append(ensemble_pred)
for ensemble_name in ensembles:
  ensemble_evaluation[ensemble_name] = {}
  ensemble_evaluation[ensemble_name]["val_predictions"] = list()
  predict_ensemble(ensemble_name, "val", val, weighted=WEIGHTED)
  ensembles[ensemble_name]["metrics"] = compute_metrics(val.get("labels").tolist(), ensemble_evaluation[ensemble_name].get("val_predictions"))  
  print(f"{ensemble_name}\t", ensembles[ensemble_name].get("metrics"))

ensemble00	 {'accuracy': 0.85809, 'macro_f1': 0.89211, 'macro_precision': 0.93471, 'macro_recall': 0.85738, 'weighted_f1': 0.89993}
ensemble01	 {'accuracy': 0.89864, 'macro_f1': 0.92486, 'macro_precision': 0.95456, 'macro_recall': 0.89841, 'weighted_f1': 0.92861}
ensemble02	 {'accuracy': 0.68351, 'macro_f1': 0.73996, 'macro_precision': 0.77952, 'macro_recall': 0.70811, 'weighted_f1': 0.7513}
ensemble03	 {'accuracy': 0.95613, 'macro_f1': 0.97132, 'macro_precision': 0.98452, 'macro_recall': 0.95872, 'weighted_f1': 0.97262}
ensemble04	 {'accuracy': 0.96702, 'macro_f1': 0.97754, 'macro_precision': 0.9932, 'macro_recall': 0.96255, 'weighted_f1': 0.97933}
ensemble05	 {'accuracy': 0.87352, 'macro_f1': 0.90232, 'macro_precision': 0.94202, 'macro_recall': 0.86808, 'weighted_f1': 0.90798}
ensemble06	 {'accuracy': 0.89924, 'macro_f1': 0.92439, 'macro_precision': 0.95952, 'macro_recall': 0.89369, 'weighted_f1': 0.9291}
ensemble07	 {'accuracy': 0.84024, 'macro_f1': 0.87703, 'macro_precision': 0.928

In [84]:
import json
with open(os.path.join(PATH, 'ensembles.json'), 'w', encoding='utf-8') as f:
    json.dump(ensembles, f, ensure_ascii=False, indent=4)

In [85]:
f1_scores = {ensemble_name: ensembles[ensemble_name]["metrics"].get("weighted_f1") for ensemble_name in ensemble_evaluation}
best_ensemble_name = max(f1_scores, key=f1_scores.get)
best_ensemble = {"name": best_ensemble_name,                 
                "models": ensembles[best_ensemble_name].get("models"),                 
                "metrics": ensembles[best_ensemble_name].get("metrics")                 
                }
best_ensemble

{'name': 'ensemble18',
 'models': ['beto-cased', 'beto-uncased'],
 'metrics': {'accuracy': 0.97035,
  'macro_f1': 0.98024,
  'macro_precision': 0.99442,
  'macro_recall': 0.96671,
  'weighted_f1': 0.98177}}

In [86]:
for model_name in models:
  model_predictions, model_raw_outputs = models.get(model_name).predict(test["text"].tolist())
  model_evaluation[model_name]["test_model_outputs"] = model_raw_outputs
  model_evaluation[model_name]["test_predictions"] = list ()  
  for output in model_raw_outputs:
    model_evaluation[model_name]["test_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output])
predict_ensemble(best_ensemble.get("name"), "test", test, weighted=WEIGHTED)

3it [00:03,  1.13s/it]                                                                                                                                                                                                                  
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 186/186 [00:02<00:00, 68.75it/s]
3it [00:03,  1.11s/it]                                                                                                                                                                                                                  
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 186/186 [00:02<00:00, 75.09it/s]
3it [00:03,  1.10s/it]                                              

In [87]:
for model_name, evaluation in model_evaluation.items():
  curr_model = model_evaluation.get(model_name)
  curr_model["val_model_outputs"] = [list(output) for output in curr_model.get("val_model_outputs")]
  curr_model["test_model_outputs"] = [list(output) for output in curr_model.get("test_model_outputs")]
  curr_model["val_predictions"] = list(curr_model.get("val_predictions"))
  curr_model["test_predictions"] = list(curr_model.get("test_predictions"))
  if curr_model.get("val_wrong_predictions"):
    curr_model["val_wrong_predictions_list"] = curr_model.get("val_wrong_predictions")
    curr_model["val_wrong_predictions"] = {}
    for pred in curr_model.get("val_wrong_predictions_list"):
      curr_model["val_wrong_predictions"][pred.guid] = {
          "text_a": pred.text_a,
          "text_b": pred.text_b,
          "label": pred.label
      }
    del curr_model["val_wrong_predictions_list"]

  with open(os.path.join(PATH, f'{model_name}/model-evaluation.json'), 'w', encoding='utf-8') as f:
    json.dump(curr_model, f, ensure_ascii=False, indent=4)

In [88]:
best_ensemble["val_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("val_predictions")
best_ensemble["test_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
with open(os.path.join(PATH, 'best-ensemble.json'), 'w', encoding='utf-8') as f:
    json.dump(best_ensemble, f, ensure_ascii=False, indent=4)

In [89]:
test["predicted_labels"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
test.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                           labels predicted_labels  
0  [None, None, None, None, None]  [0, 0, 0, 0, 1]  
1  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
2  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
3  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
4  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
5  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
6  [None, None, None, None, None]  [1, 0, 0, 0, 1]  
7  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
8  [None, None, None, None, None]  [0, 0, 0, 0, 0]  
9  [None, None, None, None, None]  [0, 0, 0, 0, 0]

In [90]:
test.to_csv(os.path.join(PATH, "test-predictions.csv"), index=False) 